In [ ]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

In [ ]:
# imports

import pandas as pd
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
import matplotlib.pyplot as plt
import pdb
import tensorflow as tf
import numpy as np
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout, Flatten, Conv2D, MaxPool2D
from tensorflow.keras.optimizers import RMSprop
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.metrics import SparseCategoricalAccuracy
from tensorflow.keras.losses import SparseCategoricalCrossentropy
import math
from IPython import display
from typing import Union, cast, List
import warnings
import os

def show(X: Union[pd.DataFrame, np.ndarray], indexes: Union[List[int], range], 
         y: Union[pd.Series, np.ndarray] = None, preds: np.ndarray = None):

    for nrows in range(1, int(math.sqrt(len(indexes)))+1):
        ncols = int(8/5 * nrows) # 8/5 column to row ratio
        if nrows * ncols > len(indexes): 
            ncols = math.ceil(len(indexes) / nrows)
            break  
    y = y.values if type(y) == pd.Series else y
    X = X.values if type(X) == pd.DataFrame else X

    assert preds is None or type(preds) == np.ndarray

    fig, ax = plt.subplots(nrows=nrows, ncols=ncols, sharex=True, sharey=True,figsize=(8, 10))
    ax = ax.flatten()
    for i, index in enumerate(indexes):
        img = X[index].reshape(28, 28)
        ax[i].imshow(img, cmap='Greys', interpolation='nearest')
        if preds is not None and y is not None:
            y = cast(np.ndarray, y)
            if len(indexes) <=25:
                title = f'label: {y[index]} pred: {preds[index]}'
            else:
                title = f'{y[index]} p:{preds[index]}'
            ax[i].set_title(title)
    for i in range(len(indexes), nrows*ncols):
        ax[i].set_visible(False)
    ax[0].set_xticks([])
    ax[0].set_yticks([])
    plt.tight_layout()
    plt.show()


seed = 20220622
url_to_data = "http://www.donwoodlock.com/ml201/25Jul2022/"

warnings.filterwarnings('ignore') 
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3' 
tf.random.set_seed(seed)
pd.options.display.max_columns = 28

In [ ]:
# load up training data
train_df = pd.read_csv(url_to_data + 'train.csv')
train_df.head()

In [ ]:
# define X and y
X = train_df.drop(columns='label') / 255
y = train_df['label']

In [ ]:
# show a single digit as a dataframe
pd.DataFrame(X.iloc[10].values.reshape(28, 28))

In [ ]:
# show the digit as an image
plt.imshow(X.iloc[10].values.reshape(28, 28), cmap='Greys')

In [ ]:
# show first 25 digits
show(X, range(25))

In [ ]:
# show first instance of each digit

show(X, [y.tolist().index(n) for n in range(10)])

In [ ]:
# show first 25 7s.
show(X, np.where(y == 7)[0][0:25])

In [ ]:
# reshape X for cnn

In [ ]:
# split X and y into training and evaluation data
X_train, X_eval, y_train, y_eval = train_test_split(X, y, random_state=seed, test_size=0.2)

In [ ]:
X_train.shape, X_eval.shape

In [ ]:
# show cnn architecture

In [62]:
# create model

model = Sequential([
  Dense(128, activation='relu'),
  Dense(10, activation='softmax')
])

model.compile(
    optimizer=Adam(),
    loss=SparseCategoricalCrossentropy(),
)

In [63]:
# train model
model.fit(X_train, y_train, epochs=30, batch_size=75, 
          validation_data = (X_eval, y_eval))

In [64]:
# make predictions on evaluation data
preds = np.argmax(model.predict(X_eval), axis=1)
preds

In [65]:
y_eval

In [66]:
# show accuracy
accuracy_score(preds, y_eval)

In [67]:
# show 25 digits
show(X_eval, range(25), y_eval, preds)

In [68]:
# show the indexes for the ones that it got wrong
np.where(y_eval != preds)[0]